# MPAGS 2023 - Optical astronomy

Welcome to the MPAGS 2023 Optical astronomy assesment.

In this notebook, you ill be reducing data for TIC-256912435 observed with the Next Generation Transit Survey (NGTS). NGTS is a quite of 12 20-cm telescopes located at Cerro Paranal, Chile, maintained by Warwick and many other institutes. In this notebook, you will reduce data observed for TIC-256912435 using aperture photometry. All images have been reduced for the sake of this assessment. 

I want you to produce:

1. A graph of MJD (modified julian date) VS raw flux for TIC-256912435.
2. A graph of MJD VS detrended flux for TIC-256912435.
3. A breif comment on what you can see in the data.

The notebook is largely complete, but there are missing variables you will be expected to fill in. 

Any problems, mail samuel.gill@warwick.ac.uk

Please mail samuel.gill@warwick.ac.uk you answers by the end of the MPAGS course, but prefarably before. Please make the header of the email "MPAGS 2023 - [your name]". 

Good luck!

### Imports

In [ ]:
import numpy as np
from astropy.io import fits
from astropy.wcs import WCS
import matplotlib.pyplot as plt
from photutils.aperture import CircularAperture
from tqdm import tqdm


### Load the data

In [ ]:
MJD = np.load('MJD.npy') # 1D array of time VS flux
DATA = np.load('DATA.npy') # 3D array of counts : time (matching MJD), X and Y
with fits.open('WCS.fits') as h : wcs = WCS(h[0].header, h)

### Lets get information about the target

You will have to fill in the RA and Dec coordinates (in degrees). Use the TIC V8 catalogue.

In [ ]:
target_tic_id = 256912435
target_ra = 
target_dec = 
x_target, y_target = wcs.all_world2pix(target_ra, target_dec, 0)
aperture_target = CircularAperture([x_target, y_target], 3.0)


### Let's plot the target

In [ ]:
fig, ax = plt.subplots(1,1)
ax.set(xlim=[x_target-100,x_target+100], ylim=[y_target-100,y_target+100])
ax.imshow(DATA[20], aspect='auto', vmin=0, vmax=5000)
aperture_target.plot(ax=ax, color='r')
plt.savefig('TIC-256912435_target.png')

If you've done this right, there will be a red circle in the middle!

### Now lets get the comparison star information

You will have to fill in the RA and Dec coordinates (in degrees). Use the TIC V8 catalogue.

In [ ]:
comp_tic_id = 256912583
comp_ra = 
comp_dec = 
x_comp, y_comp = wcs.all_world2pix(comp_ra, comp_dec, 0)
aperture_comp = CircularAperture([x_comp, y_comp], 3.0)

check_tic_id = 288462220
check_ra = 
check_dec = 
x_check, y_check = wcs.all_world2pix(check_ra, check_dec, 0)
aperture_check = CircularAperture([x_check, y_check], 3.0)


In [ ]:
fig, ax = plt.subplots(1,1)
ax.set(xlim=[x_target-100,x_target+100], ylim=[y_target-100,y_target+100])
ax.imshow(DATA[20], aspect='auto', vmin=1000, vmax=7000)
aperture_target.plot(ax=ax, color='r')
aperture_comp.plot(ax=ax, color='r')
aperture_check.plot(ax=ax, color='r')
plt.savefig('TIC-256912435_comparisons.png')

If you've done this right, there will be 3 red circles in the middle!

# OK, now lets do photometry

In [ ]:
TARGET_FLUX = np.zeros(DATA.shape[0])
COMP_FLUX = np.zeros(DATA.shape[0])
CHECK_FLUX = np.zeros(DATA.shape[0])
for i in tqdm(range(DATA.shape[0])):
    TARGET_FLUX[i] = aperture_target.do_photometry(DATA[i])[0][0]
    COMP_FLUX[i] = aperture_comp.do_photometry(DATA[i])[0][0]
    CHECK_FLUX[i] = aperture_check.do_photometry(DATA[i])[0][0]

### Lets plot the raw flux

In [ ]:
fig, ax = plt.subplots(1,1, figsize=(15,5))
ax.scatter(MJD, TARGET_FLUX, c='k')
ax.plot(MJD, TARGET_FLUX, c='k', lw=1, ls='--', alpha = 0.3)
_ = ax.set(xlabel='MJD', ylabel='Raw Flux', title='TIC-256912435 flux')
plt.savefig('TIC-256912435_raw_flux.png')

We can see very clear systematics here. We will use a comparison star to remove nightly trends caused by airmass (an other things).

### Lets check our comparison star agains the check star, to make sure it is OK to use as a comparison star

This should be flat! 

In [ ]:
fig, ax = plt.subplots(1,1, figsize=(15,5))
ax.scatter(MJD, COMP_FLUX/CHECK_FLUX, c='k')
ax.plot(MJD, COMP_FLUX/CHECK_FLUX, c='k', lw=1, ls='--', alpha = 0.3)
_ = ax.set(xlabel='MJD', ylabel='Detrended Flux', title='Comparison star validation (should be flat)')
plt.savefig('TIC-256912435_comparison_check.png')

OK, so the comparison star is good to use to detrend the raw target flux!

###  Now lets plot the results

In [ ]:
fig, ax = plt.subplots(1,1, figsize=(15,5))
ax.scatter(MJD, TARGET_FLUX/(COMP_FLUX+CHECK_FLUX), c='k')
ax.plot(MJD, TARGET_FLUX/(COMP_FLUX+CHECK_FLUX), c='k', lw=1, ls='--', alpha = 0.3)
_ = ax.set(xlabel='MJD', ylabel='Detrended Flux', title='TIC-256912435 flux')
plt.savefig('TIC-256912435_detrended_flux.png')

# Things to return

Please email samuel.gill@warwick.ac.uk the following:

1. A graph of MJD (modified julian date) VS raw flux for TIC-256912435.
2. A graph of MJD VS detrended flux for TIC-256912435.
3. A breif comment on what you can see in the data. What kind of event can you see?